In [3]:
import copy
import math
import os

import h5py
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import scipy
import torch
import torch.nn as nn
import torch.nn.functional as Func
from torch.optim import Adam
from torch.utils.data import DataLoader, Dataset, TensorDataset
from torch.utils.tensorboard import SummaryWriter
from tqdm import tqdm

%matplotlib inline

In [4]:
def plot_data(x, y, index, example, z=0, out=False):
    if out:
        fig = plt.figure(figsize=(7, 7))
        ax = fig.add_subplot(1, 3, 1)
        ax.imshow(x.squeeze())
        ax.set_title('Input x')
        ax = fig.add_subplot(1, 3, 2)
        ax.imshow(y.squeeze())
        ax.set_title('Input y')
        ax = fig.add_subplot(1, 3, 3)
        ax.imshow(y.squeeze())
        ax.set_title('Model Prediction')
        fig.suptitle(f'Visualizing sample {index} of {example} problem', y=0.76)
        fig.tight_layout()
        fig.show()
            
    else: 
        fig = plt.figure(figsize=(7, 7))
        ax = fig.add_subplot(1, 2, 1)
        ax.imshow(x.squeeze())
        ax.set_title('Input x')
        ax = fig.add_subplot(1, 2, 2)
        ax.imshow(y.squeeze())
        ax.set_title('Ouput y')
        fig.suptitle(f'Visualizing input sample {index} for {example} problem', y=0.75)
        fig.tight_layout()
        fig.show()

In [27]:
def get_group(file):
    
    with h5py.File(file, mode="r") as f:
        print("Keys",len(f.keys()))
        for group in f.keys():
            print("Group:",group, type(f[group]))
            if isinstance(f[group], h5py.Dataset):
                num_sub = f[group].shape
                print("No: of subgroup:", num_sub)
                if num_sub:
                    print("--------------------------------------")
                    for col in f[group]:
                        print("SubGroup:",col," with Shape:",col.shape)
                    print("--------------------------------------")
            else:
                num_sub = len(f[group])
                print("No: of subgroup:", num_sub)
                if num_sub:
                    print("--------------------------------------")
                    for col in f[group]:
                        print("SubGroup:",col," with Shape:",len(f[group][col]))
                    print("--------------------------------------")
            break
    f.close()

### Wave and Darcy data

In [159]:
file = "/p/project/cexalab/john2/NeuralOperators/neural_operators/data/Darcy_64x64_IN.h5"
# file = "/p/project/cexalab/john2/NeuralOperators/neural_operators/data/WaveData_64x64_IN.h5"
example = "darcy"
with h5py.File(file, "r") as f:
    
    if example == "wave":
        # t={1:10}
        # input same for all t={1:10}
        # index = {0:1999}
        # keys = 2000 + 8
        # input: u(t=0), output: u(t>0)
        t1 = 1
        t2 = 5
        index1 = 1
        index2 = 100
        x1 = torch.from_numpy(f["Sample_" + str(index1) + "_t_" + str(t1)]["input"][:]).type(torch.float32)
        y1 = torch.from_numpy(f["Sample_" + str(index1) + "_t_" + str(t1)]["output"][:]).type(torch.float32)
        x2 = torch.from_numpy(f["Sample_" + str(index2) + "_t_" + str(t2)]["input"][:]).type(torch.float32)
        y2 = torch.from_numpy(f["Sample_" + str(index2) + "_t_" + str(t2)]["output"][:]).type(torch.float32)
    else:
        # index = {0:512}
        # keys  = 512 + 5
        # input: a(x), output: u(x)
        index1 = 1
        index2 = 100
        x1 = torch.from_numpy(f["sample_" + str(index1)]["input"][:]).type(torch.float32)
        y1 = torch.from_numpy(f["sample_" + str(index1)]["output"][:]).type(torch.float32)
        x2 = torch.from_numpy(f["sample_" + str(index2)]["input"][:]).type(torch.float32)
        y2 = torch.from_numpy(f["sample_" + str(index2)]["output"][:]).type(torch.float32)
    
    print("Shape:",x1.shape, y1.shape)
    print(f"Index at {index1} with input {x1} and output{y1}")
    print(f"Index at {index2} with input {x2} and output{y2}")
    print(f"Difference in input at index {index1} and index {index2} is {np.linalg.norm(x1-x2)}")
    print(f"Difference in output at index {index1} and index {index2} is {np.linalg.norm(y1-y2)}")
f.close()


Shape: torch.Size([64, 64]) torch.Size([64, 64])
Index at 1 with input tensor([[12., 12., 12.,  ...,  3.,  3.,  3.],
        [12., 12., 12.,  ...,  3.,  3.,  3.],
        [ 3.,  3.,  3.,  ...,  3.,  3.,  3.],
        ...,
        [ 3.,  3.,  3.,  ...,  3.,  3., 12.],
        [ 3.,  3.,  3.,  ...,  3., 12., 12.],
        [ 3.,  3.,  3.,  ...,  3., 12., 12.]]) and outputtensor([[ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00],
        [ 0.0000e+00, -5.0538e-05, -8.7834e-05,  ..., -3.3615e-04,
         -1.8910e-04,  0.0000e+00],
        [ 0.0000e+00, -2.2167e-04, -3.9800e-04,  ..., -6.1382e-04,
         -3.3626e-04,  0.0000e+00],
        ...,
        [ 0.0000e+00, -3.9259e-04, -7.2712e-04,  ..., -3.9645e-04,
         -9.1797e-05,  0.0000e+00],
        [ 0.0000e+00, -2.1741e-04, -3.9308e-04,  ..., -2.1962e-04,
         -3.9540e-05,  0.0000e+00],
        [ 0.0000e+00,  0.0000e+00,  0.0000e+00,  ...,  0.0000e+00,
          0.0000e+00,  0.0000e+00]

In [149]:
get_group(file = "/p/project/cexalab/john2/NeuralOperators/neural_operators/data/WaveData_64x64_IN.h5")

Keys 20008
Group: Sample_0_t_1 <class 'h5py._hl.group.Group'>
No: of subgroup: 2
--------------------------------------
SubGroup: input  with Shape: 64
SubGroup: output  with Shape: 64
--------------------------------------
Group: Sample_0_t_10 <class 'h5py._hl.group.Group'>
No: of subgroup: 2
--------------------------------------
SubGroup: input  with Shape: 64
SubGroup: output  with Shape: 64
--------------------------------------
Group: Sample_0_t_2 <class 'h5py._hl.group.Group'>
No: of subgroup: 2
--------------------------------------
SubGroup: input  with Shape: 64
SubGroup: output  with Shape: 64
--------------------------------------
Group: Sample_0_t_3 <class 'h5py._hl.group.Group'>
No: of subgroup: 2
--------------------------------------
SubGroup: input  with Shape: 64
SubGroup: output  with Shape: 64
--------------------------------------
Group: Sample_0_t_4 <class 'h5py._hl.group.Group'>
No: of subgroup: 2
--------------------------------------
SubGroup: input  with Shape

### Rayleigh-Bernard-Data

In [6]:
def rbc_tasks(filename, ind1, ind2):
    with h5py.File(filename, mode="r") as f:
        b_0 = f["tasks"]["buoyancy"][ind1]
        b_t = f["tasks"]["buoyancy"][ind2]
        v_0 = f["tasks"]["vorticity"][ind1]
        v_t = f["tasks"]["vorticity"][ind2]
        vel_0 = f["tasks"]["velocity"][ind1]
        vel_t = f["tasks"]["velocity"][ind2]
        
        # print(f"Index {ind1}\n buoyancy: \n{b_0}\n vorticity: \n{v_0}\n velocity: \n{vel_0}")
        # print(f"Index {ind2}\n buoyancy: \n{b_t}\n vorticity: \n{v_t}\n velocity: \n{vel_t}"    
    f.close()
    return vel_0,vel_t,b_0,b_t,v_0,v_t

In [7]:
def rbc_scales(filename, ind):
    with h5py.File(filename, mode="r") as f:
        iteration = f["scales/iteration"][ind]
        sim_time  = f["scales/sim_time"][ind]
        time_step = f["scales/timestep"][ind]
        wall_time = f["scales/wall_time"][ind]
        
        # print("Constant", f["scales/constant"][:])
        # print("Iteration", f["scales/iteration"][:].shape)
        # print("Simulation Time", f["scales/sim_time"][:].shape)
        # print("timestep", f["scales/timestep"][:].shape)
        # print("Wall time", f["scales/wall_time"][:].shape)
        # print("write number", f["scales/write_number"][:])
        # print("X", f["scales/x_hash_259ff677ed0cf648980d6e69fe3d2deb0dc82141"][:].shape)
        # print("Z", f["scales/z_hash_2b3e6c1ad6197e7bbb577c37c9be3babe1727daf"][:].shape)   
    f.close()
    return iteration, sim_time, time_step, wall_time

In [37]:
rbc_scales('/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/training_data/snapshots_1_tf_50_seed_2648_s1.h5',-1)

(2245, 49.75509013021564, 0.016348931587292816, 101.77322888374329)

In [150]:
get_group('/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/training_data/snapshots_2_tf_50_seed_1186_s1.h5')

Keys 2
Group: scales <class 'h5py._hl.group.Group'>
No: of subgroup: 8
--------------------------------------
SubGroup: constant  with Shape: 1
SubGroup: iteration  with Shape: 200
SubGroup: sim_time  with Shape: 200
SubGroup: timestep  with Shape: 200
SubGroup: wall_time  with Shape: 200
SubGroup: write_number  with Shape: 200
SubGroup: x_hash_259ff677ed0cf648980d6e69fe3d2deb0dc82141  with Shape: 256
SubGroup: z_hash_2b3e6c1ad6197e7bbb577c37c9be3babe1727daf  with Shape: 64
--------------------------------------
Group: tasks <class 'h5py._hl.group.Group'>
No: of subgroup: 3
--------------------------------------
SubGroup: buoyancy  with Shape: 200
SubGroup: velocity  with Shape: 200
SubGroup: vorticity  with Shape: 200
--------------------------------------


## Training Data

In [12]:
# Training Data: /p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/training_data
# u_0 = 0, b_0 = random.(seed=random.randint(1,5000), distribution='normal', scale=1e-3), t_0= 0, tf=50, Ra=10e4, Pr=1
# Compressed File: /p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50.h5
# Group: snapshots_{index:0:250}_t_{0:50}
# Subgroup: velocity_0 - (2,256,64), u_0
# Subgroup: velocity_t - (2,256,64), u_t
# -------------------------------------------------------
# Subgroup: tasks/buoyancy_0 - (256,64), b_0
# Subgroup: tasks/buoyancy_t - (256,64), b_t
# Subgroup: tasks/vorticity_0 - (256,64), v_0
# Subgroup: tasks/vorticity_t - (256,64), v_t
# -------------------------------------------------------
# SubGroup: scales/iteration  
# SubGroup: scales/sim_time  
# SubGroup: scales/timestep  
# SubGroup: scales/wall_time  

In [22]:
filename = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_train.h5"
foldername = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/training_data"
with h5py.File(filename, "w") as data:
    for index,file in enumerate(os.listdir(foldername)):
        for t in range(51):
            vel_0, vel_t,b_0,b_t,v_0,v_t = rbc_tasks(os.path.join(foldername,file),0,t)
            # print(vel_0, vel_t)
            iteration, sim_time, time_step, wall_time = rbc_scales(os.path.join(foldername,file),t)
            data[f'snapshots_{index}_t_{t}/scales/iteration'] = iteration
            data[f'snapshots_{index}_t_{t}/scales/sim_time'] = sim_time
            data[f'snapshots_{index}_t_{t}/scales/timestep'] = time_step
            data[f'snapshots_{index}_t_{t}/scales/wall_time'] = wall_time
            data[f'snapshots_{index}_t_{t}/velocity_0'] = vel_0
            data[f'snapshots_{index}_t_{t}/tasks/buoyancy_0'] = b_0
            data[f'snapshots_{index}_t_{t}/tasks/vorticity_0'] = v_0
            data[f'snapshots_{index}_t_{t}/velocity_t'] = vel_t
            data[f'snapshots_{index}_t_{t}/tasks/buoyancy_t'] = b_t
            data[f'snapshots_{index}_t_{t}/tasks/vorticity_t'] = v_t
     
                

In [14]:
get_group('/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_train.h5')

Keys 12750
Group: snapshots_0_t_0 <class 'h5py._hl.group.Group'>
No: of subgroup: 4
--------------------------------------
SubGroup: scales  with Shape: 4
SubGroup: tasks  with Shape: 4
SubGroup: velocity_0  with Shape: 2
SubGroup: velocity_t  with Shape: 2
--------------------------------------


In [59]:
filename = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_train.h5"
foldername = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/training_data"
for index,file in enumerate(os.listdir(foldername)):
    # for t in range(0,200,10):
        # vel_0, vel_t,b_0,b_t,v_0,v_t = rbc_tasks(os.path.join(foldername,file),0,t)
    iteration, sim_time, time_step, wall_time = rbc_scales(os.path.join(foldername,file),0)
    print(iteration, sim_time, time_step, wall_time)
 

0 0.0 0.125 6.649348735809326
0 0.0 0.125 6.888504981994629
0 0.0 0.125 6.70348596572876
0 0.0 0.125 6.597389221191406
0 0.0 0.125 6.781322956085205
0 0.0 0.125 6.698441505432129
0 0.0 0.125 6.673957109451294
0 0.0 0.125 6.7096452713012695
0 0.0 0.125 6.62915825843811
0 0.0 0.125 6.668988227844238
0 0.0 0.125 7.150238275527954
0 0.0 0.125 6.740588188171387
0 0.0 0.125 6.9596030712127686
0 0.0 0.125 6.648501873016357
0 0.0 0.125 6.7478132247924805
0 0.0 0.125 6.651765823364258
0 0.0 0.125 6.655501365661621
0 0.0 0.125 6.607147455215454
0 0.0 0.125 6.69962739944458
0 0.0 0.125 6.736853122711182
0 0.0 0.125 6.720532178878784
0 0.0 0.125 6.875074148178101
0 0.0 0.125 6.686131238937378
0 0.0 0.125 6.791266202926636
0 0.0 0.125 6.658910036087036
0 0.0 0.125 6.704341888427734
0 0.0 0.125 6.709383726119995
0 0.0 0.125 6.782572507858276
0 0.0 0.125 6.733569622039795
0 0.0 0.125 6.744348764419556
0 0.0 0.125 6.710951328277588
0 0.0 0.125 6.676116704940796
0 0.0 0.125 6.779739856719971
0 0.0 0.12

## Validation Data

In [15]:
# Validation Data: /p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/validation_data
# u_0 = 0, b_0 = random.(seed=random.randint(1,5000), distribution='normal', scale=1e-3), t_0= 0, tf=50, Ra=10e4, Pr=1
# Compressed File: /p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_val.h5
# Group: snapshots_{index:0:100}_t_{0:199}
# Subgroup: velocity_0 - (2,256,64), u_0
# Subgroup: velocity_t - (2,256,64), u_t
# -------------------------------------------------------
# Subgroup: tasks/buoyancy_0 - (256,64), b_0
# Subgroup: tasks/buoyancy_t - (256,64), b_t
# Subgroup: tasks/vorticity_0 - (256,64), v_0
# Subgroup: tasks/vorticity_t - (256,64), v_t
# -------------------------------------------------------
# SubGroup: scales/iteration  
# SubGroup: scales/sim_time  
# SubGroup: scales/timestep  
# SubGroup: scales/wall_time  

In [33]:
filename = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_val.h5"
foldername = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/validation_data"
with h5py.File(filename, "w") as data:
    for index,file in enumerate(os.listdir(foldername)):
        for t in range(51):
            vel_0, vel_t,b_0,b_t,v_0,v_t = rbc_tasks(os.path.join(foldername,file),0,t)
            # print(vel_0, vel_t)
            iteration, sim_time, time_step, wall_time = rbc_scales(os.path.join(foldername,file),t)
            data[f'snapshots_{index}_t_{t}/scales/iteration'] = iteration
            data[f'snapshots_{index}_t_{t}/scales/sim_time'] = sim_time
            data[f'snapshots_{index}_t_{t}/scales/timestep'] = time_step
            data[f'snapshots_{index}_t_{t}/scales/wall_time'] = wall_time
            data[f'snapshots_{index}_t_{t}/velocity_0'] = vel_0
            data[f'snapshots_{index}_t_{t}/tasks/buoyancy_0'] = b_0
            data[f'snapshots_{index}_t_{t}/tasks/vorticity_0'] = v_0
            data[f'snapshots_{index}_t_{t}/velocity_t'] = vel_t
            data[f'snapshots_{index}_t_{t}/tasks/buoyancy_t'] = b_t
            data[f'snapshots_{index}_t_{t}/tasks/vorticity_t'] = v_t

In [34]:
get_group('/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_val.h5')

Keys 5100
Group: snapshots_0_t_0 <class 'h5py._hl.group.Group'>
No: of subgroup: 4
--------------------------------------
SubGroup: scales  with Shape: 4
SubGroup: tasks  with Shape: 4
SubGroup: velocity_0  with Shape: 2
SubGroup: velocity_t  with Shape: 2
--------------------------------------


In [56]:
filename = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_val.h5"
foldername = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/validation_data"
for index,file in enumerate(os.listdir(foldername)):
    # for t in range(0,200,10):
        # vel_0, vel_t,b_0,b_t,v_0,v_t = rbc_tasks(os.path.join(foldername,file),0,t)
    iteration, sim_time, time_step, wall_time = rbc_scales(os.path.join(foldername,file),50)
    print(iteration, sim_time, time_step, wall_time)
 

100 12.5 0.125 11.230997800827026
100 12.5 0.125 11.224835872650146
100 12.5 0.125 11.145978212356567
100 12.5 0.125 11.155580759048462
100 12.5 0.125 11.359298944473267
100 12.5 0.125 11.255656957626343
100 12.5 0.125 11.10475754737854
100 12.5 0.125 11.119298696517944
100 12.5 0.125 11.231040954589844
100 12.5 0.125 11.211319923400879
100 12.5 0.125 11.091270685195923
100 12.5 0.125 11.173965215682983
100 12.5 0.125 11.213322639465332
100 12.5 0.125 11.073866367340088
100 12.5 0.125 11.162525177001953
100 12.5 0.125 11.065159797668457
100 12.5 0.125 11.157073259353638
100 12.5 0.125 11.326671361923218
100 12.5 0.125 11.338244199752808
100 12.5 0.125 11.223374843597412
100 12.5 0.125 11.190888166427612
100 12.5 0.125 11.247129440307617
100 12.5 0.125 11.049216508865356
100 12.5 0.125 11.248018264770508
100 12.5 0.125 11.217379570007324
100 12.5 0.125 11.329625368118286
100 12.5 0.125 11.312412738800049
100 12.5 0.125 11.666171789169312
100 12.5 0.125 11.102998971939087
100 12.5 0.125 

## Test Data

In [18]:
# Test Data: /p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/test_data
# u_0 = 0, b_0 = random.(seed=random.randint(1,5000), distribution='normal', scale=1e-3), t_0= 0, tf=50, Ra=10e4, Pr=1
# Compressed File: /p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_test.h5
# Group: snapshots_{index:0:100}_t_{0:199}
# Subgroup: velocity_0 - (2,256,64), u_0
# Subgroup: velocity_t - (2,256,64), u_t
# -------------------------------------------------------
# Subgroup: tasks/buoyancy_0 - (256,64), b_0
# Subgroup: tasks/buoyancy_t - (256,64), b_t
# Subgroup: tasks/vorticity_0 - (256,64), v_0
# Subgroup: tasks/vorticity_t - (256,64), v_t
# -------------------------------------------------------
# SubGroup: scales/iteration  
# SubGroup: scales/sim_time  
# SubGroup: scales/timestep  
# SubGroup: scales/wall_time  

In [19]:
# filename = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_test.h5"
# foldername = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/test_data"
# with h5py.File(filename, "w") as data:
#     for index,file in enumerate(os.listdir(foldername)):
#         for t in range(51):
#             vel_0, vel_t,b_0,b_t,v_0,v_t = rbc_tasks(os.path.join(foldername,file),0,t)
#             # print(vel_0, vel_t)
#             iteration, sim_time, time_step, wall_time = rbc_scales(os.path.join(foldername,file),t)
#             data[f'snapshots_{index}_t_{t}/scales/iteration'] = iteration
#             data[f'snapshots_{index}_t_{t}/scales/sim_time'] = sim_time
#             data[f'snapshots_{index}_t_{t}/scales/timestep'] = time_step
#             data[f'snapshots_{index}_t_{t}/scales/wall_time'] = wall_time
#             data[f'snapshots_{index}_t_{t}/velocity_0'] = vel_0
#             data[f'snapshots_{index}_t_{t}/tasks/buoyancy_0'] = b_0
#             data[f'snapshots_{index}_t_{t}/tasks/vorticity_0'] = v_0
#             data[f'snapshots_{index}_t_{t}/velocity_t'] = vel_t
#             data[f'snapshots_{index}_t_{t}/tasks/buoyancy_t'] = b_t
#             data[f'snapshots_{index}_t_{t}/tasks/vorticity_t'] = v_t

In [52]:
get_group('/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_test.h5')

Keys 5100
Group: snapshots_0_t_0 <class 'h5py._hl.group.Group'>
No: of subgroup: 4
--------------------------------------
SubGroup: scales  with Shape: 4
SubGroup: tasks  with Shape: 4
SubGroup: velocity_0  with Shape: 2
SubGroup: velocity_t  with Shape: 2
--------------------------------------


In [57]:
filename = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/RBC_NX256_NZ64_TF50_test.h5"
foldername = "/p/project/cexalab/john2/NeuralOperators/RayleighBernardConvection/test_data"
for index,file in enumerate(os.listdir(foldername)):
    # for t in range(0,200,10):
        # vel_0, vel_t,b_0,b_t,v_0,v_t = rbc_tasks(os.path.join(foldername,file),0,t)
    iteration, sim_time, time_step, wall_time = rbc_scales(os.path.join(foldername,file),50)
    print(iteration, sim_time, time_step, wall_time)
 

100 12.5 0.125 11.25784707069397
100 12.5 0.125 11.283603429794312
100 12.5 0.125 11.125366449356079
100 12.5 0.125 11.32484483718872
100 12.5 0.125 11.185351133346558
100 12.5 0.125 11.16381549835205
100 12.5 0.125 11.233612775802612
100 12.5 0.125 11.130318880081177
100 12.5 0.125 11.073821544647217
100 12.5 0.125 11.286361932754517
100 12.5 0.125 11.269673347473145
100 12.5 0.125 11.186192512512207
100 12.5 0.125 11.17392086982727
100 12.5 0.125 11.181200504302979
100 12.5 0.125 11.281229257583618
100 12.5 0.125 11.195455551147461
100 12.5 0.125 11.150555610656738
100 12.5 0.125 11.212627649307251
100 12.5 0.125 11.161268711090088
100 12.5 0.125 11.155949831008911
100 12.5 0.125 11.296412944793701
100 12.5 0.125 11.188637495040894
100 12.5 0.125 11.137947082519531
100 12.5 0.125 11.204299211502075
100 12.5 0.125 11.239294528961182
100 12.5 0.125 11.224326133728027
100 12.5 0.125 11.167171239852905
100 12.5 0.125 11.261767625808716
100 12.5 0.125 11.16361379623413
100 12.5 0.125 11.1